**Carga las tres librerías de siempre** 

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pylab as plt

**La data que vamos a usar en este ejercicio corresponde a varias medidas geométricas hechas sobre tres variedades de trigo. Carga y crea un dataframe de pandas a partir del fichero .txt. Este fichero es un txt y no un csv, así  que seguramente tengas que usar otra función que no sea `read_csv`. Puedes mirar en la documentación de __[pandas](https://pandas.pydata.org/pandas-docs/stable/io.html)__ para saber qué función usar**

In [ ]:
dat_seeds = pd.read_table('data_3.txt',header=None)

**Muestra en pantalla info sobre los tipos de las columnas y de si tienen NaNs. Asimismo, muestra en pantalla información estadística de cada columna, con su medía, quartiles....** 

In [ ]:
dat_seeds.info()

In [ ]:
dat_seeds.describe()

**Las siete primeras columnas corresponden a las features y la última al target. Cambia por tanto el nombre de las columnas a ['area', 'perimeter', 'compactness', 'kernel-length', 'kernel-width', 'asymmetry-coefficient', 'kernel-groove-length', 'variety']**

In [ ]:
dat_seeds.columns= ['area', 'perimeter', 
  'compactness', 'kernel-length', 
  'kernel-width', 'asymmetry-coefficient', 'kernel-groove-length', 
  'variety']

**Crea una matrix numpy `X` con las features y un array `y` con las variedades de trigo**

In [ ]:
X = dat_seeds.drop(columns=['variety']).values
y = dat_seeds['variety'].values

**Vamos tratar algún algoritmo de clustering sobre estos datos ( la matriz X de features). Para ello, antes de nada, estandariza esto datos usando la clase de scikit correspondiente** 

In [ ]:
from sklearn.preprocessing import StandardScaler

ss = StandardScaler()

X_scaled = ss.fit_transform(X)

**Usa Kmeans para ver cómo de buena es la reconstrucción de los clusters. Mide esto usando cualquiera de las métricas vistas en clase. Cuando definas el objeto de la clase Kmeans, elige `n_clusters` = 3 (puesto que sabemos que debería haber 3 clases), `random_state` = 0, para que sea reproducible y `n_init` = 100 para asegurarnos encontrar el mejor resultado posible** 

In [ ]:
from sklearn.cluster import KMeans
from sklearn.metrics import adjusted_rand_score, adjusted_mutual_info_score, completeness_score, homogeneity_score
km = KMeans(n_clusters = 3, random_state=0, n_init=100)
km.fit(X_scaled)

print("adjusted rand score = " , adjusted_rand_score(y, km.predict(X_scaled)))
print("adjusted mutual info score = " , adjusted_mutual_info_score(y, km.predict(X_scaled)))
print("completeness score = " , completeness_score(y, km.predict(X_scaled)))
print("homogeneity score = " , homogeneity_score(y, km.predict(X_scaled)))

In [ ]:
from sklearn.cluster import AgglomerativeClustering
agg = AgglomerativeClustering(n_clusters = 3)

y_pred = agg.fit_predict(X_scaled)

print("adjusted rand score = " , adjusted_rand_score(y, y_pred))
print("adjusted mutual info score = " , adjusted_mutual_info_score(y, y_pred))
print("completeness score = " , completeness_score(y, y_pred))
print("homogeneity score = " , homogeneity_score(y, y_pred))

In [ ]:
from sklearn.mixture import GaussianMixture
gm = GaussianMixture(n_components = 3, n_init=100, random_state=0)

gm.fit(X_scaled)

y_pred = gm.predict(X_scaled)
print("adjusted rand score = " , adjusted_rand_score(y, y_pred))
print("adjusted mutual info score = " , adjusted_mutual_info_score(y, y_pred))
print("completeness score = " , completeness_score(y, y_pred))
print("homogeneity score = " , homogeneity_score(y, y_pred))

**Usa el método elbow para mostrar que en efecto el número de clusters óptimo es 3. Acuérdate de que, una vez fitteado el KMeans, el atributo *inertia_* nos daba la información que necesaria que teníamos que plotear mediante el método elbow**

In [ ]:
res = []
for k in np.arange(1,10):

    km = KMeans(n_clusters = k, random_state=0)
    km.fit(X_scaled)
    res.append(km.inertia_)

plt.plot( np.arange(1,10), res)

**(Opcional) Calcula la matriz de correlaciones entre las features y plotead esta matriz. Para calcular la matriz de correlaciones puedes usar la función `corrcoef` de numpy o usar el método `corr` que tiene los data frames de pandas. Cuidado porque si usas la función de numpy, la correlación la hace entre las filas y a nosotros nos interesan las columnas, esto es, los features. En este caso, cuando usas `corrcoef`, tienes que elegir el argumento `rowvar` = False o bien transponer la matriz antes de llamar a este método. Para plotear esta matriz de correlaciones, puedes usar el método `imshow` de matplotlib**

In [ ]:
plt.imshow(np.corrcoef(X, rowvar=False))
plt.colorbar()

**Realiza una pca sobre la matriz de features (estandarizada, obviamente), de tal manera que nos dé aquellas componentes que expliquen el 95 % de la varianza de los datos. Transforma los datos originales al espacio de las componentes seleccionadas por la PCA**

In [ ]:
from sklearn.decomposition import PCA
pca = PCA(n_components=0.95)
X_pca = pca.fit_transform(X_scaled)

In [ ]:
pca.n_components_

**Haz scatter plots entre las diferentes componentes principales. Puedes ver el número de componentes calculadas accediendo al atributo `n_components_` una vez ajustada la PCA. Acuérdate de que para hacer un scatter plot tienes que usar la función `scatter` de matplotlib. Pásale como argumento `c` el vector de targets y.** 

In [ ]:
plt.scatter(X_pca[:,0],X_pca[:,1], c=y)

In [ ]:
plt.scatter(X_pca[:,0],X_pca[:,2], c=dat_seeds.iloc[:,7])

In [ ]:
plt.scatter(X_pca[:,1],X_pca[:,2], c=dat_seeds.iloc[:,7])

**Muestra de nuevo el rendimiento del clustering usando KMeans, pero ahora sobre la matriz de datos transformados por la PCA al espacio de las componentes principales**

In [ ]:
km = KMeans(n_clusters = 3, random_state=0, n_init=100)
km.fit(X_pca)
y_pred = km.predict(X_pca)
print("adjusted rand score = " , adjusted_rand_score(y, y_pred))
print("adjusted mutual info score = " , adjusted_mutual_info_score(y, y_pred))
print("completeness score = " , completeness_score(y, y_pred))
print("homogeneity score = " , homogeneity_score(y, y_pred))

In [ ]:
gm = GaussianMixture(n_components = 3, n_init=100, random_state=0)
gm.fit(X_pca)
y_pred = gm.predict(X_pca)

print("adjusted rand score = " , adjusted_rand_score(y, y_pred))
print("adjusted mutual info score = " , adjusted_mutual_info_score(y, y_pred))
print("completeness score = " , completeness_score(y, y_pred))
print("homogeneity score = " , homogeneity_score(y, y_pred))

**Uno de los atributos del objeto de la pca cuando lo hemos fitteado es `components_`, que muestra el peso de cada feature en cada componente. Plotea el output de llamar a este atributo usando el metodo `imshow` de matplotlib**

In [ ]:
plt.imshow(pca.components_, cmap = plt.cm.bwr)
plt.colorbar()